# Введение

Необходимо найти способ определения уровня сложности английского языка в фильмах по субтитрам.

Предоставлены данные:

- английские словари Oxford, в которых слова распределены по уровню сложности
- набор файлов-субтитров, рассортированных по каталогам в соответствии с уровнем сложности
- excel файл со список несортированных фильмов и указанием их уровня

Цель: создание модели определения уровня сложности

Установка библиотек

In [1]:
# !pip install pysrt

In [2]:
# !pip install pip setuptools wheel
# !pip install spacy
# !python -m spacy download en_core_web_sm

In [3]:
# !pip install xgboost

Импорт необходимых библиотек

In [59]:
import pandas as pd
import numpy as np

import os
import re
import random
import pysrt
import spacy

from sklearn.model_selection import cross_val_score
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder
import xgboost as xgb

# настройки вывода ошибок
import warnings
warnings.filterwarnings("ignore", category=FutureWarning)

# настройки отображения
pd.set_option('display.max_rows', None)

Откроем данные. Сначала таблицу с метками уровней в формате xlsx

In [5]:
movies_labels = pd.read_excel('C:/Users/Alexander Malfington/Desktop/English_level/English_scores/movies_labels.xlsx')

In [6]:
movies_labels = movies_labels.drop('id', axis=1)

In [7]:
movies_labels

Movie       Level
0                            10_Cloverfield_lane(2016)          B1
1                     10_things_I_hate_about_you(1999)          B1
2                                 A_knights_tale(2001)          B2
3                                 A_star_is_born(2018)          B2
4                                        Aladdin(1992)      A2/A2+
5                          All_dogs_go_to_heaven(1989)      A2/A2+
6                               An_American_tail(1986)      A2/A2+
7                                           Babe(1995)      A2/A2+
8                             Back_to_the_future(1985)      A2/A2+
9                             Banking_On_Bitcoin(2016)          C1
10                                 Batman_begins(2005)      A2/A2+
11                          Beauty_and_the_beast(2017)          B2
12                          Before_I_go_to_sleep(2014)          B2
13                                Before_sunrise(1995)      B1, B2
14                                 Before_sunset(2004)      B1, B2
15                                    Braveheart(1995)          B2
16                           Bridget_Jones_diary(2001)      B1, B2
17                                 Bridget_Joness_Baby          C1
18                                          Cars(2006)          B1
19                                     Cast_away(2000)      A2/A2+
20                           Catch_me_if_you_can(2002)      B1, B2
21                   Charlie_and_the_Chocolate_Factory          B1
22                                    Cinderella(1950)          B1
23                                      Clueless(1995)          B1
24                                      Deadpool(2016)          B2
25                                 Despicable_Me(2010)          B2
26                                      Die_hard(1988)          B1
27                                         Dredd(2012)      A2/A2+
28                                          Dune(2021)          B2
29                                  Enola_Holmes(2020)          B2
30                                          Entrapment          B2
31                      Eurovision_song_contest_(2020)      A2/A2+
32                                     Ferdinand(2017)          B1
33                                    Fight_club(1999)          B2
34                                  Finding_Nemo(2003)      A2/A2+
35                                  Forrest_Gump(1994)  A2/A2+, B1
36                             Good_Will_Hunting(1997)          B2
37                                 Groundhog_day(1993)          B1
38                                        Powder(1995)          B1
39                                           Her(2013)  A2/A2+, B1
40                                    Home_alone(1990)          B1
41                                          Hook(1991)      A2/A2+
42                                House_of_Gucci(2021)          B2
43                                    Inside_out(2015)          B1
44                                    Inside_out(2015)          B1
45                          Its_a_wonderful_life(1946)      A2/A2+
46                                         Klaus(2019)          C1
47                                    Knives_out(2019)          B2
48                      Kubo_and_the_two_strings(2016)      A2/A2+
49                                     Liar_liar(1997)          B1
50                                          Lion(2016)      B1, B2
51                                         Logan(2017)          B1
52                                 Love_actually(2003)          B1
53                                 Made_of_Honor(2008)          B2
54                                     Mamma_Mia(2008)          B1
55                          Mary_Poppins_returns(2018)          B1
56                                       Matilda(1996)          B1
57                              Meet_the_parents(2000)          B1
58                                        Milada(2017)          B1
59                           

Поскольку данные разбросаны по каталогам и таблицам, для начала необходимо сверить данные из таблицы с фактически имеющимися субтитрами и их метками. Для этого спарсим названия файлов и попытаемся сопоставить их с табличными данными, чтобы найти сходства и отличия.

К каждому файлу добавим информацию о том, в каком каталоге он содержится, поскольку в названиях каталогов закодирована информация об уровнt сложности.

In [8]:
dirs = ['A2', 'B1', 'B2', 'C1', 'Subtitles']
parsed_dirs = pd.DataFrame(columns=['Movie', 'Level'])

In [9]:
for dir_ in dirs:
    dir_path = 'C:/Users/Alexander Malfington/Desktop/English_level/English_scores/Subtitles_all/' + dir_
    file_names = os.listdir(dir_path)
    parsed_dirs = parsed_dirs.append(pd.DataFrame({'Movie': file_names, 'Level': dir_}), ignore_index=True)

In [10]:
parsed_dirs

Movie      Level
0    The Walking Dead-S01E01-Days Gone Bye.English.srt         A2
1             The Walking Dead-S01E02-Guts.English.srt         A2
2    The Walking Dead-S01E03-Tell It To The Frogs.E...         A2
3            The Walking Dead-S01E04-Vatos.English.srt         A2
4         The Walking Dead-S01E05-Wildfire.English.srt         A2
5            The Walking Dead-S01E06-TS-19.English.srt         A2
6                         AmericanBeauty1999.BRRip.srt         B1
7                      Angelas.Christmas.Wish.2020.srt         B1
8    Indiana Jones And The Last Crusade DVDRip Xvid...         B1
9                           mechanic-resurrection_.srt         B1
10       Men.In.Black.1997.720p.Bluray.x264-SEPTiC.srt         B1
11       Rat.Race.2001.1080p.WEB-DL.DD5.1.H264-FGT.srt         B1
12   Seven.Worlds.One.Planet.S01E01.2160p.BluRay.Re...         B1
13   Seven.Worlds.One.Planet.S01E02.2160p.BluRay.Re...         B1
14   Seven.Worlds.One.Planet.S01E03.2160p.BluRay.Re...         B1
15   Seven.Worlds.One.Planet.S01E04.2160p.BluRay.Re...         B1
16   Seven.Worlds.One.Planet.S01E05.2160p.BluRay.Re...         B1
17   Seven.Worlds.One.Planet.S01E06.2160p.BluRay.Re...         B1
18   Seven.Worlds.One.Planet.S01E07.2160p.BluRay.Re...         B1
19                        SlingShot (2014) WEB.eng.srt         B1
20              Spirit.Stallion.of.the.Cimarron.EN.srt         B1
21             Terminator_2_Judgment_Day_1991_roNy.srt         B1
22             Valentine's.Day.2010.Subtitles.YIFY.srt         B1
23          Angela's.Christmas.2018.WEBRip.Netflix.srt         B2
24   Collateral.Beauty.2016.720p.BRRip.x264.AAC-ETR...         B2
25   Crazy4TV.com - Suits.S06E01.720p.BluRay.x265.H...         B2
26   Crazy4TV.com - Suits.S06E02.720p.BluRay.x265.H...         B2
27   Crazy4TV.com - Suits.S06E03.720p.BluRay.x265.H...         B2
28   Crazy4TV.com - Suits.S06E04.720p.BluRay.x265.H...         B2
29   Crazy4TV.com - Suits.S06E05.720p.BluRay.x265.H...         B2
30   Crazy4TV.com - Suits.S06E06.720p.BluRay.x265.H...         B2
31   Crazy4TV.com - Suits.S06E07.720p.BluRay.x265.H...         B2
32   Crazy4TV.com - Suits.S06E08.720p.BluRay.x265.H...         B2
33   Crazy4TV.com - Suits.S06E09.720p.BluRay.x265.H...         B2
34   Crazy4TV.com - Suits.S06E10.720p.BluRay.x265.H...         B2
35   Crazy4TV.com - Suits.S06E11.720p.BluRay.x265.H...         B2
36   Crazy4TV.com - Suits.S06E12.720p.BluRay.x265.H...         B2
37   Crazy4TV.com - Suits.S06E13.720p.BluRay.x265.H...         B2
38   Crazy4TV.com - Suits.S06E14.720p.BluRay.x265.H...         B2
39   Crazy4TV.com - Suits.S06E15.720p.BluRay.x265.H...         B2
40   Crazy4TV.com - Suits.S06E16.720p.BluRay.x265.H...         B2
41     Crown, The S01E01 - Wolferton Splash.en.SDH.srt         B2
42         Crown, The S01E01 - Wolferton Splash.en.srt         B2
43     Crown, The S01E02 - Hyde Park Corner.en.SDH.srt         B2
44         Crown, The S01E02 - Hyde Park Corner.en.srt         B2
45           Crown, The S01E03 - Windsor.en.FORCED.srt         B2
46              Crown, The S01E03 - Windsor.en.SDH.srt         B2
47                  Crown, The S01E03 - Windsor.en.srt         B2
48           Crown, The S01E04 - Act of God.en.SDH.srt         B2
49               Crown, The S01E04 - Act of God.en.srt         B2
50   Crown, The S01E05 - Smoke and Mirrors.en.FORCE...         B2
51    Crown, The S01E05 - Smoke and Mirrors.en.SDH.srt         B2
52        Crown, The S01E05 - Smoke and Mirrors.en.srt         B2
53            Crown, The S01E06 - Gelignite.en.SDH.srt         B2
54                Crown, The S01E06 - Gelignite.en.srt         B2
55   Crown, The S01E07 - Scientia Potentia Est.en.F...         B2
56   Crown, The S01E07 - Scientia Potentia Est.en.S...         B2
57    Crown, The S01E07 - Scientia Potentia Est.en.srt         B2
58          Crown, The S01E08 - Pride & Joy.en.SDH.srt         B2
59              Crown, The S01E08 - Pride & Joy.en.srt         B2
60            Crown, Th

Впоследствии каталог Subtitles будет заменен на имеющуюся информацию из xlsx файла.

In [11]:
#избавляемся от расширений имён файлов
parsed_dirs['Movie'] = parsed_dirs['Movie'].str.replace('.srt', '')

#удаляем ненужный системный файл .DS_Store
parsed_dirs = parsed_dirs.drop(163)

In [12]:
parsed_dirs.head(5)

Movie Level
0      The Walking Dead-S01E01-Days Gone Bye.English    A2
1               The Walking Dead-S01E02-Guts.English    A2
2  The Walking Dead-S01E03-Tell It To The Frogs.E...    A2
3              The Walking Dead-S01E04-Vatos.English    A2
4           The Walking Dead-S01E05-Wildfire.English    A2

Объединим две таблицы

In [13]:
merged_movies = pd.merge(movies_labels, parsed_dirs, on='Movie', how='outer') \
.rename(columns={'Level_x': 'Given Table', 'Level_y': 'Given Subs'})

In [14]:
merged_movies

Movie Given Table Given Subs
0                            10_Cloverfield_lane(2016)          B1  Subtitles
1                     10_things_I_hate_about_you(1999)          B1  Subtitles
2                                 A_knights_tale(2001)          B2  Subtitles
3                                 A_star_is_born(2018)          B2  Subtitles
4                                        Aladdin(1992)      A2/A2+  Subtitles
5                          All_dogs_go_to_heaven(1989)      A2/A2+  Subtitles
6                               An_American_tail(1986)      A2/A2+  Subtitles
7                                           Babe(1995)      A2/A2+  Subtitles
8                             Back_to_the_future(1985)      A2/A2+  Subtitles
9                             Banking_On_Bitcoin(2016)          C1  Subtitles
10                                 Batman_begins(2005)      A2/A2+  Subtitles
11                          Beauty_and_the_beast(2017)          B2  Subtitles
12                          Before_I_go_to_sleep(2014)          B2  Subtitles
13                                Before_sunrise(1995)      B1, B2  Subtitles
14                                 Before_sunset(2004)      B1, B2  Subtitles
15                                    Braveheart(1995)          B2  Subtitles
16                           Bridget_Jones_diary(2001)      B1, B2  Subtitles
17                                 Bridget_Joness_Baby          C1  Subtitles
18                                          Cars(2006)          B1  Subtitles
19                                     Cast_away(2000)      A2/A2+  Subtitles
20                           Catch_me_if_you_can(2002)      B1, B2  Subtitles
21                   Charlie_and_the_Chocolate_Factory          B1  Subtitles
22                                    Cinderella(1950)          B1  Subtitles
23                                      Clueless(1995)          B1  Subtitles
24                                      Deadpool(2016)          B2  Subtitles
25                                 Despicable_Me(2010)          B2  Subtitles
26                                      Die_hard(1988)          B1  Subtitles
27                                         Dredd(2012)      A2/A2+  Subtitles
28                                          Dune(2021)          B2  Subtitles
29                                  Enola_Holmes(2020)          B2  Subtitles
30                                          Entrapment          B2  Subtitles
31                      Eurovision_song_contest_(2020)      A2/A2+  Subtitles
32                                     Ferdinand(2017)          B1  Subtitles
33                                    Fight_club(1999)          B2  Subtitles
34                                  Finding_Nemo(2003)      A2/A2+  Subtitles
35                                  Forrest_Gump(1994)  A2/A2+, B1  Subtitles
36                             Good_Will_Hunting(1997)          B2  Subtitles
37                                 Groundhog_day(1993)          B1  Subtitles
38                                        Powder(1995)          B1  Subtitles
39                                        Powder(1995)          B1  Subtitles
40                                           Her(2013)  A2/A2+, B1  Subtitles
41                                    Home_alone(1990)          B1  Subtitles
42                                          Hook(1991)      A2/A2+  Subtitles
43                                House_of_Gucci(2021)          B2  Subtitles
44                                    Inside_out(2015)          B1  Subtitles
45                                    Inside_out(2015)          B1  Subtitles
46                          Its_a_wonderful_life(1946)      A2/A2+  Subtitles
47                                         Klaus(2019)          C1  Subtitles
48                                    Knives_out(2019)          B2  Subtitles
49                      Kubo_and_the_two_strings(2016)      A2/A2+  Subtitles
50                                     Liar_liar(1997)          B1  Sub

Субтитры без информации об уровне используемого языка не берем, т.к. нет хорошего источника по определению уровня языка. Скачаны недостающие субтитры, для которых есть информация об уровне сложности:
- The Secret Life of Pets
- Glass Onion, Matilda (2022)
- Bullet train
- Thor: love and thunder
- Lightyear
- The Grinch

Несоответсвия названий:
- Up (2009)
- SOMM.Into.the.Bottle.2015
- Gullivers.Travels.1939

Скачаем все субтитры с помощью библиотеки pysrt

In [15]:
dir_path = 'C:/Users/Alexander Malfington/Desktop/English_level/English_scores/Subtitles_all/'
srt_files = [os.path.join(root, file) for root, _, files in os.walk(dir_path) for file in files if file.endswith('.srt')]

In [16]:
subs = pd.DataFrame(columns=['Subs', 'Movie'])

for i in range(len(srt_files)):
    try:
        subs.loc[i, 'Subs'] = pysrt.open(srt_files[i])
        subs.loc[i, 'Movie'] = os.path.basename(srt_files[i]).replace('.srt', '')
    except:
        subs.loc[i, 'Subs'] = pysrt.open(srt_files[i], encoding='iso-8859-1')
        subs.loc[i, 'Movie'] = os.path.basename(srt_files[i]).replace('.srt', '')

In [17]:
subs.head()

Subs          Movie
0  [1\n00:00:16,500 --> 00:00:26,500\n<font color...   Bullet train
1  [1\n00:00:26,458 --> 00:00:29,625\nNo, subject...    Glass Onion
2  [1\n00:00:09,134 --> 00:00:12,137\n(HEROIC MUS...      Lightyear
3  [1\n00:01:03,292 --> 00:01:06,417\n[chiming mu...  Matilda(2022)
4  [1\n00:00:20,289 --> 00:00:25,289\n\n, 2\n00:0...     The Grinch

Субтритры записаны в датафрейм. Объединим таблицы.

In [18]:
data = pd.merge(subs, merged_movies, on='Movie', how='outer')

In [19]:
data

Subs  \
0    [1\n00:00:16,500 --> 00:00:26,500\n<font color...   
1    [1\n00:00:26,458 --> 00:00:29,625\nNo, subject...   
2    [1\n00:00:09,134 --> 00:00:12,137\n(HEROIC MUS...   
3    [1\n00:01:03,292 --> 00:01:06,417\n[chiming mu...   
4    [1\n00:00:20,289 --> 00:00:25,289\n\n, 2\n00:0...   
5    [1\n00:00:30,407 --> 00:00:33,368\nIlluminatio...   
6    [1\n00:00:41,933 --> 00:00:43,977\nOh, great a...   
7    [1\n00:00:03,169 --> 00:00:05,171\n( bugs chit...   
8    [1\n00:00:03,045 --> 00:00:05,047\n- ( birds c...   
9    [1\n00:00:03,003 --> 00:00:04,671\n( thunder r...   
10   [1\n00:00:03,045 --> 00:00:05,422\n( birds chi...   
11   [1\n00:00:03,420 --> 00:00:04,922\n- ( walkie-...   
12   [1\n00:00:03,086 --> 00:00:06,215\n- ( people ...   
13   [1\n00:00:32,672 --> 00:00:36,634\nI need a fa...   
14   [1\n00:00:30,840 --> 00:00:31,960\nWhere are w...   
15   [0\n00:01:57,283 --> 00:01:58,716\nDismount!\n...   
16   [1\n00:02:59,920 --> 00:03:01,592\nMr. Santos,...   
17   [1\n00:02:58,849 --> 00:03:00,642\nGoddamn bug...   
18   [1\n00:00:50,217 --> 00:00:52,344\nWell, I wak...   
19   [1\n00:00:22,023 --> 00:00:23,983\n200 million...   
20   [1\n00:00:37,038 --> 00:00:41,959\nAsia - the ...   
21   [1\n00:00:37,830 --> 00:00:40,583\nAt the sout...   
22   [1\n00:00:40,917 --> 00:00:42,627\nAustralia -...   
23   [1\n00:00:35,912 --> 00:00:38,372\nEurope.\n, ...   
24   [1\n00:00:44,462 --> 00:00:47,506\nOne contine...   
25   [1\n00:00:50,176 --> 00:00:51,677\nAfrica.\n, ...   
26   [1\n00:00:27,628 --> 00:00:29,697\nHere's some...   
27   [1\n00:00:36,883 --> 00:00:46,554\n''Spirit St...   
28   [1\n00:01:17,545 --> 00:01:22,550\n3 billion h...   
29   [1\n00:00:30,179 --> 00:00:34,775\n<i>Hey ther...   
30   [1\n00:00:06,080 --> 00:00:08,520\n[match snap...   
31   [1\n00:00:10,000 --> 00:00:15,000\n<font color...   
32   [1\n00:00:00,877 --> 00:00:02,253\n<font color...   
33   [1\n00:00:01,002 --> 00:00:02,295\n<font color...   
34   [1\n00:00:01,002 --> 00:00:02,504\n<font color...   
35   [1\n00:00:00,877 --> 00:00:02,337\n(HARVEY REA...   
36   [1\n00:00:01,044 --> 00:00:02,420\n<font color...   
37   [1\n00:00:00,877 --> 00:00:02,337\n(HARVEY REA...   
38   [1\n00:00:00,960 --> 00:00:02,337\n<font color...   
39   [1\n00:00:00,960 --> 00:00:02,462\n<font color...   
40   [1\n00:00:01,002 --> 00:00:02,420\n<font color...   
41   [1\n00:00:01,044 --> 00:00:02,295\n<font color...   
42   [1\n00:00:02,419 --> 00:00:04,099\n<font color...   
43   [1\n00:00:02,294 --> 00:00:04,054\n<font color...   
44   [1\n00:00:02,336 --> 00:00:04,384\n<i><b>What ...   
45   [1\n00:00:02,503 --> 00:00:04,380\n<font color...   
46   [1\n00:00:02,252 --> 00:00:04,346\n<font color...   
47   [1\n00:00:02,294 --> 00:00:04,262\n<font color...   
48   [1\n00:00:10,640 --> 00:00:14,560\n[coughing]\...   
49   [1\n00:00:59,400 --> 00:01:03,960\nIn seeking ...   
50   [1\n00:00:16,040 --> 00:00:19,480\n"My husband...   
51   [1\n00:00:16,040 --> 00:00:19,480\n"My husband...   
52   [1\n00:30:13,960 --> 00:30:16,520\nDear Aunt, ...   
53   [1\n00:00:11,960 --> 00:00:16,400\n[child]<i> ...   
54   [1\n00:00:11,960 --> 00:00:16,400\n<i> Gina! G...   
55   [1\n00:00:10,800 --> 00:00:12,800\n[doors crea...   
56   [1\n00:00:27,680 --> 00:00:29,800\n- Fuel on.\...   
57   [1\n00:41:36,960 --> 00:41:39,960\n<i>For the ...   
58   [1\n00:00:15,040 --> 00:00:17,040\n[brass band...   
59   [1\n00:00:29,240 --> 00:00:32,000\nYes.\n, 2\n...   
60   [1\n00:00:31,480 --> 00:00:33,400\n[fanfare pl...   
61   [1\n00:00:36,760 --> 00:00:39,960\n<i>More tha...   
62   [1\n00:00:44,760 --> 00:00:46,520\nYour Majest...   
63   [1\n00:00:44,760 --> 00:00:46,520\n[woman spea...   
64   [1\n00:00:44,760 --> 00:00:46,520\nYour Majest...   
65   [1\n00:00:34,360 --> 00:00:37,760\n-Ask my dau...   
66   [1\n00:00:34,360 --> 00:00:37,760\n-Ask my dau...   
67   [1\n00:00:15,120 --> 00:00:19,520\n<i>♪ If you...   
68   [1\n00:00:35,960 --> 00:00:37,040\nThis way

Подкорректируем информацию, удалим строки с дублирующейся информацией.

In [20]:
data.loc[6, 'Given Table'] = 'B2'
data = data.drop([289,290,291])

Нужно объединить две колонки, содержащие информацию об уровне сложности. Если информации нет ни в одном из истоников - удалим строки.

In [21]:
data['Level'] = 'WHOKNOWS'

for i in range(len(data)):
    if pd.notnull(data['Given Table'][i]) and (pd.isnull(data['Given Subs'][i]) or data['Given Subs'][i] == 'Subtitles'):
        data['Level'][i] = data['Given Table'][i]
    elif data['Given Table'][i] == data['Given Subs'][i]:
        data['Level'][i] = data['Given Table'][i]
    elif pd.isnull(data['Given Table'][i]) and (pd.notnull(data['Given Subs'][i]) and data['Given Subs'][i] != 'Subtitles'):
        data['Level'][i] = data['Given Subs'][i]

In [22]:
data.head()

Subs          Movie  \
0  [1\n00:00:16,500 --> 00:00:26,500\n<font color...   Bullet train   
1  [1\n00:00:26,458 --> 00:00:29,625\nNo, subject...    Glass Onion   
2  [1\n00:00:09,134 --> 00:00:12,137\n(HEROIC MUS...      Lightyear   
3  [1\n00:01:03,292 --> 00:01:06,417\n[chiming mu...  Matilda(2022)   
4  [1\n00:00:20,289 --> 00:00:25,289\n\n, 2\n00:0...     The Grinch   

  Given Table Given Subs Level  
0          B1        NaN    B1  
1          B2        NaN    B2  
2          B2        NaN    B2  
3          C1        NaN    C1  
4          B1        NaN    B1

In [23]:
data = data.drop(['Given Table', 'Given Subs'], axis=1)
data = data.loc[~(data.Level == 'WHOKNOWS')]

In [24]:
print('Всего субтитров:', len(data))
data.head()

Всего субтитров: 281


Subs          Movie Level
0  [1\n00:00:16,500 --> 00:00:26,500\n<font color...   Bullet train    B1
1  [1\n00:00:26,458 --> 00:00:29,625\nNo, subject...    Glass Onion    B2
2  [1\n00:00:09,134 --> 00:00:12,137\n(HEROIC MUS...      Lightyear    B2
3  [1\n00:01:03,292 --> 00:01:06,417\n[chiming mu...  Matilda(2022)    C1
4  [1\n00:00:20,289 --> 00:00:25,289\n\n, 2\n00:0...     The Grinch    B1

In [25]:
data.loc[0,'Subs'].text

'<font color="#FF9966"><i>♫  Columbia Pictures Fanfare playing  ♫</i></font>\n<font color="#00CDCD">(monitor beeping rhythmically)</font>\n<font color="#00CDCD">(respirator whooshing\nrhythmically)</font>\n<font color="#00CDCD">(rhythmic beeping and whooshing\ncontinue)</font>\n<font color="#00CDCD">(rhythmic beeping and whooshing\ncontinue)</font>\n<font color="#00CDCD">(creaking)</font>\n<font color="#00CDCD">(cries softly, sniffles)</font>\n<font color="#00CDCD">(animated music plays on TV)</font>\n<font color="#FF9966"><i>♫  ♫</i></font>\nThe boom slang was stolen\nfrom the zoo last night.\nIt\'s extremely dangerous.\n<font color="#00CDCD">(rhythmic beeping and whooshing\ncontinue)</font>\n<font color="#00CDCD">(sighing)</font>\n<font color="#00CDCD">(P.A. beeps)</font>\n<font color="#00CDCD">(indistinct announcement\nover P.A.)</font>\n<font color="#00CDCD">(rhythmic beeping and whooshing\ncontinue)</font>\nFather.\nAny news on my grandson?\nNo change.\nHe hasn\'t woken up.\nA fat

Субтитры загружены, дубликаты очищены, всего с учетом загруженных недостающих субтитров имеем 281 файл.

Субтитры содержат очень много мусора, тегов. Напишем функцию для очистики.

In [26]:
HTML = r'<.*?>' # html тэги меняем на пробел
TAG = r'{.*?}' # тэги меняем на пробел
COMMENTS = r'[\(\[][A-Za-z ]+[\)\]]' # комменты в скобках меняем на пробел
UPPER = r'[[A-Za-z ]+[\:\]]' # указания на того кто говорит (BOBBY:)
LETTERS = r'[^a-zA-Z\'.,!? ]' # все что не буквы меняем на пробел 
SPACES = r'([ ])\1+' # повторяющиеся пробелы меняем на один пробел
DOTS = r'[\.]+' # многоточие меняем на точку
SYMB = r"[^\w\d'\s]" # знаки препинания кроме апострофа

def clean_subs(subs):
    subs = subs[1:] # удаляем первый рекламный субтитр
    txt = re.sub(HTML, ' ', subs.text) # html тэги меняем на пробел
    txt = re.sub(COMMENTS, ' ', txt) # комменты в скобках меняем на пробел
    txt = re.sub(UPPER, ' ', txt) # указания на того кто говорит (BOBBY:)
    txt = re.sub(LETTERS, ' ', txt) # все что не буквы меняем на пробел
    txt = re.sub(DOTS, r'.', txt) # многоточие меняем на точку
    txt = re.sub(SPACES, r'\1', txt) # повторяющиеся пробелы меняем на один пробел
    txt = re.sub(SYMB, '', txt) # знаки препинания кроме апострофа на пустую строку
    txt = re.sub('www', '', txt) # кое-где остаётся www, то же меняем на пустую строку
    txt = txt.lstrip() # обрезка пробелов слева
    txt = txt.encode('ascii', 'ignore').decode() # удаляем все что не ascii символы   
    txt = txt.lower() # текст в нижний регистр
    return txt

In [27]:
clean_subs(data.loc[0,'Subs'])

"respirator whooshing rhythmically rhythmic beeping and whooshing continue rhythmic beeping and whooshing continue cries softly sniffles the boom slang was stolen from the zoo last night it's extremely dangerous rhythmic beeping and whooshing continue pa beeps indistinct announcement over pa rhythmic beeping and whooshing continue father any news on my grandson no change he hasn't woken up a father's job is to protect his family when wataru was on that roof policeman talking over speaker when he was pushed where was his father wataru is lucky you never know what horrible fate your bad luck has saved you from an stayin' alive by avu chan playing an improved by sailor an hope you enjoy the show an stayin' alive sung in japanese stayin' alive stayin' alive stayin' alive thank you for taking the job on such short notice i am ready you are getting the new and improved me since i've been working with barry i am experiencing a calm like never before never like i'm less reactive to situations 

Очистика работает, теперь нужно применить ее ко всем субтитрам построчно.

In [28]:
data['Subs'] = data['Subs'].apply(clean_subs)

In [29]:
data.head()

Subs          Movie Level
0  respirator whooshing rhythmically rhythmic bee...   Bullet train    B1
1  hey oh shit sorry let me uh uh sign here can y...    Glass Onion    B2
2  buzz lightyear mission log stardate  sensors h...      Lightyear    B2
3  my mummy says i'm a miracle my daddy says i'm ...  Matilda(2022)    C1
4  i illumination yeah illumination whoo ha ha ha...     The Grinch    B1

Готово, проверим целевой признак.

In [30]:
data.Level.value_counts()

B2            140
B1             56
C1             40
A2/A2+         26
B1, B2          8
A2              6
A2/A2+, B1      5
Name: Level, dtype: int64

Будем исходить из того, что если для фильма указана сразу сложность и B1, и B2, то имеет смысл оставить только верхнюю сложность, поскольку это предполагает знание всех уровней ниже.

- A2/A2+ - A2
- A2/A2+, B1 - B1
- B1, B2 - B2

In [31]:
replacement_dict = {'A2/A2+': 'A2', 'A2/A2+, B1': 'B1', 'B1, B2': 'B2'}

In [32]:
data['Level'] = data['Level'].replace(replacement_dict)

In [33]:
data.Level.value_counts()

B2    148
B1     61
C1     40
A2     32
Name: Level, dtype: int64

Уровни очищены от неоднозначных значений.

Закодируем их.

In [34]:
def level_to_code(level):
    code_dict = {'A2': 0, 'B1': 1, 'B2': 2, 'C1': 3}
    return code_dict.get(level, None)

data['Level_code'] = data['Level'].apply(level_to_code)

In [35]:
data.Level_code.value_counts()

2    148
1     61
3     40
0     32
Name: Level_code, dtype: int64

In [36]:
data_before = data.copy()
data_before.head()

Subs          Movie Level  \
0  respirator whooshing rhythmically rhythmic bee...   Bullet train    B1   
1  hey oh shit sorry let me uh uh sign here can y...    Glass Onion    B2   
2  buzz lightyear mission log stardate  sensors h...      Lightyear    B2   
3  my mummy says i'm a miracle my daddy says i'm ...  Matilda(2022)    C1   
4  i illumination yeah illumination whoo ha ha ha...     The Grinch    B1   

   Level_code  
0           1  
1           2  
2           2  
3           3  
4           1

In [37]:
# data = data.drop(['Movie', 'Level'], axis=1)

In [38]:
# data.head()

Приступим к токенизации с помощью spacy.

In [39]:
nlp = spacy.load("en_core_web_sm")

Напишем функцию, которая будет извлекать усредненный вектор всех токенов за исключением стоп-слов для каждого текста (субтитра), применим ее построчно.

In [40]:
def vectorize(text):
    doc = nlp(text)
    # получение вектора текста из усредненных векторов токенов, исключая стоп-слова
    return np.mean([token.vector for token in doc if not token.is_stop], axis=0)

In [41]:
data['Vectors'] = data['Subs'].apply(vectorize)

Разделим выборку.

In [42]:
X_train, X_test, y_train, y_test = train_test_split(data['Vectors'], data['Level_code'], test_size=0.2)

Обучим модель.

In [43]:
dtrain = xgb.DMatrix(X_train.tolist(), label=y_train.tolist())

In [44]:
params = {'objective': 'multi:softmax', 'num_class': 4}
model = xgb.train(params, dtrain)

In [45]:
dtest = xgb.DMatrix(X_test.tolist())
preds = model.predict(dtest)

Изменим Accuracy на тестовой выборке.

In [47]:
accuracy = sum(preds == y_test) / len(y_test)
print("Accuracy: ", accuracy)

Accuracy:  0.5964912280701754


Попробуем использовать немного другой подход, который позволит посмотреть близость текста к каждой из категорий.

In [48]:
params_prob = {'objective': 'multi:softprob', 'num_class': 4}

In [49]:
model_prob = xgb.train(params_prob, dtrain)

In [50]:
dtest_prob = xgb.DMatrix(X_test.tolist())
preds_prob = model_prob.predict(dtest_prob)

In [64]:
pd.DataFrame(preds_prob, columns=['A2', 'B1', 'B2', 'C1']).head(10).applymap(lambda x: "{:.0%}".format(x))

A2   B1   B2   C1
0  25%  13%  57%   5%
1   2%   2%   4%  92%
2   3%  40%  54%   4%
3   3%   5%  90%   3%
4   7%  53%  36%   3%
5   4%   2%  14%  80%
6   2%   2%  93%   3%
7   4%   4%  85%   7%
8   6%   4%  86%   4%
9   5%   5%  68%  22%

Такой способо в удобном формате может вывести вероятность отнесения текста к той или иной категории. Это может быть более удобно, чем вслепую доверять модели.

Попробуем использовать векторизацию через TfidfVectorizer, для этого для начала необходимо лемматизировать тексты. Создадим новую колонку с леммами.

In [65]:
from sklearn.feature_extraction.text import TfidfVectorizer

def lemma_to_vector(text):
    #объект spacy
    doc = nlp(text)
    # получение лемм, исключая стоп-слова
    lemmatized = [token.lemma_ for token in doc if not token.is_stop]
    return lemmatized

In [66]:
data['Lemmas'] = data['Subs'].apply(lemma_to_vector)

In [67]:
data['Lemmas']

0      [respirator, whoosh, rhythmically, rhythmic, b...
1      [hey, oh, shit, sorry, let, uh, uh, sign, grab...
2      [buzz, lightyear, mission, log, stardate,  , s...
3      [mummy, say, miracle, daddy, say, special, lit...
4      [illumination, yeah, illumination, whoo, ha, h...
5      [live, city, life, max, lucky, dog, new, york,...
6      [pray, water, sustenance, pray, daughter, tire...
7      [little, girl, policeman, little, girl, afraid...
8      [mom, right, luck, tell, poison, uh, sure, way...
9      [right, hear, bitch, get, problem, bring, man,...
10     [dad, teach, tie, nail, knot, fisherman, knot,...
11     [know, know, hear, maybe, listen, right, hope,...
12     [hey, hey, whoa, whoa, whoa, whoa, ma'am, ma'a...
13     [go, spray, short, bring, girlfriend, home, sc...
14     [come, angela, mind, sheep, dada, want, hear, ...
15     [herman, horse, sick, chap, wander, passageway...
16     [save, usual, table, mr, santo, thank, pleasur...
17     [oh, shit, oh, crap, nic

Леммы созданы, разделим выборку.

In [68]:
X_train_lemmas, X_test_lemmas, y_train_lemmas, y_test_lemmas = train_test_split(data['Lemmas'], data['Level_code'], test_size=0.2)

In [69]:
X_train_lemmas.shape, X_test_lemmas.shape, y_train_lemmas.shape, y_test_lemmas.shape

((224,), (57,), (224,), (57,))

Для того, чтобы TfidfVectorizer принял данные, их нужно подавать с специальном виде, протестируем его.

In [70]:
X_train_lemmas.apply(lambda x: ' '.join(x)).tolist()

["katrina bennett say deal offer job bribe bet ass decide farm case let guess daniel hardman bait breach confidentiality ready bite drag young pretty child bearing age thing fire name defendant gender discrimination case sue folsom food thing capitulate man case afford way slice go bleed dry reputation line close maria sheila think meet ms dana scott scottie harvey oh know go harvard law long associate love tell essay go harvard london get married harvey like hanley folsom president folsom food recently victim terrible allegation discriminate woman place like marysville place woman want job want home family support want advancement support get food suck make mean bullshit pie okay image mind eat thank get vomit bagel fece pancake look care say man will promote woman want steal page book check hot mic footage interview cameraman sound guy take need catch guy lie try hire investigator authorization got kick care need talk resource hear client ' call return hardman seven case fast track r

In [71]:
vectorizer = TfidfVectorizer().fit(X_train_lemmas.apply(lambda x: ' '.join(x)).tolist())

In [72]:
X_train_lemmas = vectorizer.transform(X_train_lemmas.apply(lambda x: ' '.join(x)).tolist()).toarray()
X_test_lemmas = vectorizer.transform(X_test_lemmas.apply(lambda x: ' '.join(x)).tolist()).toarray()

Данные векторизированы, обучим модель.

In [73]:
dtrain_lemmas = xgb.DMatrix(X_train_lemmas, label=y_train_lemmas.tolist())

In [74]:
params_lemmas = {'objective': 'multi:softmax', 'num_class': 4}
model_lemmas = xgb.train(params_lemmas, dtrain_lemmas)

In [75]:
dtest_lemmas = xgb.DMatrix(X_test_lemmas)
preds_lemmas = model_lemmas.predict(dtest_lemmas)

In [76]:
accuracy = sum(preds_lemmas == y_test_lemmas) / len(y_test_lemmas)
print("Accuracy: ", accuracy)

Accuracy:  0.631578947368421


При использовании данного способа получилось несколько увеличить Accuracy.

Можно сделать вывод, что имеющего массива данных недостаточно для обучения качественной модели. Также в массиве не хватает информации о фильмах со сложностью A1 и C2.